In [1]:
import warnings
warnings.filterwarnings('ignore')

import sys
sys.path.append('/home/rupali/Documents/Master Thesis/jenga')

In [2]:
import random
import numpy as np
import pandas as pd

from sklearn.linear_model import SGDClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer

from jenga.basis import Dataset
from jenga.corruptions.generic import MissingValues, SwappedValues, CategoricalShift
from jenga.corruptions.numerical import Scaling, GaussianNoise
from jenga.cleaning.ppp import PipelinePerformancePrediction
from jenga.cleaning.outlier_detection import NoOutlierDetection, PyODKNNOutlierDetection, PyODIsolationForestOutlierDetection
from jenga.cleaning.imputation import NoImputation, MeanModeImputation
from jenga.cleaning.clean import Clean

In [3]:
## use categorical columns as strings
def cat_cols_to_str(df):
    for col in df.columns:
        if pd.api.types.is_categorical_dtype(df[col]):
            df[col] = df[col].astype(str)

    return df

/home/rupali/.local/lib/python3.8/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [4]:
def run_experiment(dataset_name, learner, param_grid, corruptions, fraction, cleaners, num_repetitions, categorical_precision_threshold=0.7, numerical_std_error_threshold=2.0):
    
    ## dataset
    dataset = Dataset(dataset_name)
    
    all_data = dataset.all_data
    attribute_names = dataset.attribute_names
    attribute_types = dataset.attribute_types
    
    ## categorical and numerical features
    categorical_columns = dataset.categorical_columns
    numerical_columns = dataset.numerical_columns
    print(f"Found {len(categorical_columns)} categorical and {len(numerical_columns)} numeric features \n")
    
    ## train and test data
    df_train, lab_train, df_test, lab_test = dataset.get_train_test_data()
    ### if we don't convert the categorical columns to str, the swapping corruption doesn't let us assign new values to the column: "Cannot setitem on a Categorical with a new category, set the categories first"
    #df_train = cat_cols_to_str(df_train)
    #df_test = cat_cols_to_str(df_test)
    
    ## pipeline performance prediction (ppp)
    ppp = PipelinePerformancePrediction(df_train, lab_train, df_test, lab_test, categorical_columns, numerical_columns, learner, param_grid)
    ppp_model = ppp.fit_ppp(df_train)
    
    ## generate corrupted data
    for _ in range(num_repetitions):
        df_corrupted, perturbations, cols_perturbed, summary_col_corrupt = ppp.get_corrupted(df_test, corruptions, fraction, num_repetitions)
    
    ## cleaning
    clean = Clean(df_train, df_corrupted, categorical_columns, numerical_columns, categorical_precision_threshold, numerical_std_error_threshold, ppp, ppp_model, cleaners)
    df_outliers, df_cleaned, corrupted_score_ppp, best_cleaning_score, cleaner_scores_ppp, summary_cleaners = clean(df_train, df_test, df_corrupted, cols_perturbed)
    
    ## results
    result = {
        'ppp_score_model': ppp.predict_score_ppp(ppp_model, df_test),
        'ppp_score_corrupted': corrupted_score_ppp,
        'ppp_score_cleaned': best_cleaning_score,
        'ppp_scores_cleaners': cleaner_scores_ppp
    }
#     print('\n'.join([f'{key}:{val}' for key, val in result.items()]))
    
    ## summary
    summary = {
        'dataset': dataset_name,
        'model': learner,
        'corruptions': summary_col_corrupt,
        'cleaners': summary_cleaners,
        'result': result
    }
#     print('\n\n\n\n'.join([f'{key}:{val}' for key, val in summary.items()]))
    
    return summary #summary_col_corrupt, result

### Altogether

In [5]:
datasets = [
    'thoracic_surgery',
    'cleve',
    'acute-inflammations'
]

In [6]:
## model parameters
## models is a dict where key = leaner & value = param_grid
models = {SGDClassifier(loss='log'): {'learner__max_iter': [500, 1000, 5000], 
                                         'learner__penalty': ['l2', 'l1', 'elasticnet'], 
                                         'learner__alpha': [0.0001, 0.001, 0.01, 0.1]
                                        }, 
          RandomForestClassifier():{'learner__n_estimators': [100, 200, 500], 
                                    'learner__max_depth': [5, 10, 15]
                                   }
         }

## make dict of multiple leraners and corresponding param_grids

In [7]:
corruptions = [[MissingValues], 
               #[SwappedValues], 
               [CategoricalShift],
               [Scaling], 
               [GaussianNoise],
               [MissingValues, CategoricalShift, Scaling, GaussianNoise]]#, SwappedValues]]

In [8]:
fractions = [0.15, 0.25, 0.5, 0.75, 0.9]

In [9]:
cleaners = [
    (NoOutlierDetection, MeanModeImputation),
    (PyODKNNOutlierDetection, MeanModeImputation),
    (PyODIsolationForestOutlierDetection, MeanModeImputation),
]

In [10]:
# stdoutOrigin=sys.stdout 
# sys.stdout = open("/home/rupali/Documents/Master Thesis/jenga/out/experiments.txt", "w")

# for _ in range(10):
#   print("\n\n..................................ITERATION..................................\n")
ind_results = []

for dataset in datasets:
    for learner, param_grid in models.items():
        for corruption in corruptions:
            for fraction in fractions:
                print(learner)
                ind_results.append(run_experiment(dataset, learner, param_grid, corruption, fraction, cleaners, 100))
        
# sys.stdout.close()
# sys.stdout=stdoutOrigin

SGDClassifier(loss='log')
Dataset: thoracic_surgery
Found 13 categorical and 3 numeric features 

Fitting 5 folds for each of 36 candidates, totalling 180 fits

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE32', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE10', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE7', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE14', 'fraction': 0.15, 'sampling': 'MCAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE17', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	per


Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE4', 'fraction': 0.15, 'sampling': 'MCAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE11', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE32', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE11', 'fraction': 0.15, 'sampling': 'MCAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'AGE', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE17', 'fraction': 0.15, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturba

/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))



Outlier detection method: PyODKNNOutlierDetection, Outlier Detection Score: {'Precision': 1.0, 'Recall': 1.0, 'F1-score': 1.0, 'Accuracy': 1.0}
Imputation method: MeanModeImputation, Imputation Score: {'Precision': 0.990625, 'Recall': 0.9511363636363637, 'F1-score': 0.9687483870967742, 'Accuracy': 0.9680851063829787, 'Mean Squared Error': nan}
Cleaner: (PyODKNNOutlierDetection, MeanModeImputation): {'roc_auc_score': 0.6489451476793249, 'classification_report': {'F': {'precision': 0.8409090909090909, 'recall': 0.9367088607594937, 'f1-score': 0.8862275449101796, 'support': 79}, 'T': {'precision': 0.16666666666666666, 'recall': 0.06666666666666667, 'f1-score': 0.09523809523809522, 'support': 15}, 'accuracy': 0.7978723404255319, 'macro avg': {'precision': 0.5037878787878788, 'recall': 0.5016877637130802, 'f1-score': 0.49073282007413743, 'support': 94}, 'weighted avg': {'precision': 0.7333172147001935, 'recall': 0.7978723404255319, 'f1-score': 0.7600058242178257, 'support': 94}}}

Outlier 


Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE6', 'fraction': 0.25, 'sampling': 'MAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'AGE', 'fraction': 0.25, 'sampling': 'MCAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE11', 'fraction': 0.25, 'sampling': 'MNAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE25', 'fraction': 0.25, 'sampling': 'MCAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE25', 'fraction': 0.25, 'sampling': 'MCAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbation: MissingValues: {'column': 'PRE4', 'fraction': 0.25, 'sampling': 'MCAR', 'na_value': nan}

Generating corrupted training data on 94 rows... 

	perturbati

...

	perturbation: Scaling: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MCAR'}
	perturbation: GaussianNoise: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MAR'}

Generating corrupted training data on 24 rows... 

	perturbation: MissingValues: {'column': 'V2', 'fraction': 0.9, 'sampling': 'MCAR', 'na_value': nan}
	perturbation: CategoricalShift: {'column': 'V4', 'fraction': 0.9, 'sampling': 'MCAR'}
	perturbation: Scaling: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MCAR'}
	perturbation: GaussianNoise: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MCAR'}

Generating corrupted training data on 24 rows... 

	perturbation: MissingValues: {'column': 'V5', 'fraction': 0.9, 'sampling': 'MCAR', 'na_value': nan}
	perturbation: CategoricalShift: {'column': 'V3', 'fraction': 0.9, 'sampling': 'MAR'}
	perturbation: Scaling: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MNAR'}
	perturbation: GaussianNoise: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MAR'}

Generating corrupted training data o


	perturbation: MissingValues: {'column': 'V5', 'fraction': 0.9, 'sampling': 'MCAR', 'na_value': nan}
	perturbation: CategoricalShift: {'column': 'V3', 'fraction': 0.9, 'sampling': 'MAR'}
	perturbation: Scaling: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MAR'}
	perturbation: GaussianNoise: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MCAR'}

Generating corrupted training data on 24 rows... 

	perturbation: MissingValues: {'column': 'V5', 'fraction': 0.9, 'sampling': 'MNAR', 'na_value': nan}
	perturbation: CategoricalShift: {'column': 'V3', 'fraction': 0.9, 'sampling': 'MCAR'}
	perturbation: Scaling: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MAR'}
	perturbation: GaussianNoise: {'column': 'V1', 'fraction': 0.9, 'sampling': 'MAR'}

Generating corrupted training data on 24 rows... 

	perturbation: MissingValues: {'column': 'V2', 'fraction': 0.9, 'sampling': 'MCAR', 'na_value': nan}
	perturbation: CategoricalShift: {'column': 'V4', 'fraction': 0.9, 'sampling': 'MCAR'}
	perturbati

/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-p

Cleaner: (NoOutlierDetection, MeanModeImputation): {'roc_auc_score': 0.8464285714285714, 'classification_report': {'no': {'precision': 1.0, 'recall': 0.7142857142857143, 'f1-score': 0.8333333333333333, 'support': 14}, 'yes': {'precision': 0.7142857142857143, 'recall': 1.0, 'f1-score': 0.8333333333333333, 'support': 10}, 'accuracy': 0.8333333333333334, 'macro avg': {'precision': 0.8571428571428572, 'recall': 0.8571428571428572, 'f1-score': 0.8333333333333333, 'support': 24}, 'weighted avg': {'precision': 0.8809523809523809, 'recall': 0.8333333333333334, 'f1-score': 0.8333333333333334, 'support': 24}}}

Outlier detection method: PyODKNNOutlierDetection, Outlier Detection Score: {'Precision': 0.765625, 'Recall': 0.875, 'F1-score': 0.7777777777777778, 'Accuracy': 0.78125}
Imputation method: MeanModeImputation, Imputation Score: {'Precision': 0.4635265700483091, 'Recall': 0.3352272727272727, 'F1-score': 0.28396135265700484, 'Accuracy': 0.3541666666666667, 'Mean Squared Error': 3.33060185185

/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1245: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-p

In [11]:
# stdoutOrigin=sys.stdout 
# sys.stdout = open("/home/rupali/Documents/Master Thesis/jenga/out/results.txt", "w")

# print(ind_results)
ind_results

# sys.stdout.close()
# sys.stdout=stdoutOrigin

/home/rupali/.local/lib/python3.8/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[{'dataset': 'thoracic_surgery',
  'model': SGDClassifier(loss='log'),
  'corruptions': defaultdict(list,
              {('DGN',): [MissingValues: {'column': 'DGN', 'fraction': 0.15, 'sampling': 'MAR', 'na_value': nan}]}),
  'cleaners': [{'Outlier detection method': NoOutlierDetection,
    'Outlier Detection Score': {'Precision': 0.425531914893617,
     'Recall': 0.5,
     'F1-score': 0.4597701149425288,
     'Accuracy': 0.851063829787234},
    'Imputation method': MeanModeImputation,
    'Imputation Score': {'Precision': 0.990625,
     'Recall': 0.9511363636363637,
     'F1-score': 0.9687483870967742,
     'Accuracy': 0.9680851063829787,
     'Mean Squared Error': nan},
    'PPP score with cleaning': {'roc_auc_score': 0.6151898734177215,
     'classification_report': {'F': {'precision': 0.8426966292134831,
       'recall': 0.9493670886075949,
       'f1-score': 0.8928571428571428,
       'support': 79},
      'T': {'precision': 0.2,
       'recall': 0.06666666666666667,
       'f1-sco